# Understand embeddings with Word2Vec

### Exercise objectives:
- Convert words to vector representations thanks to embeddings
- Discover the powerful Word2Vec algorithm

<hr>

_Embeddings_ are representations of words thanks to vectors. These embeddings can be learned within a Neural Network. But it can take time to converge. Another option is to learn them as a first step. Then, use them directly to feed the word representation into an RNN. 



# The data

Keras provides many datasets, among which is the ÌMDB dataset: it is comprised of sentences that are movie reviews. Each of them is related to a score given by the review writer.

❓ **Question** ❓ Let's first load the data. You don't have to understand what is going on in the function, it does not matter here.

⚠️ **Warning** ⚠️ The `load_data` function has a `percentage_of_sentences` argument. Depending on your computer, there are chances that too many sentences will make your compute slow down, or even freeze - your RAM can overflow. For that reason, **you should start with 10% of the sentences** and see if your computer handles it. Otherwise, rerun with a lower number.  

⚠️ **DISCLAIMER** ⚠️ **No need to play _who has the biggest_ (RAM) !** The idea is to get to run your models quickly to prototype. Even in real life, it is recommended that you start with a subset of your data to loop and debug quickly. So increase the number only if you are into getting the best accuracy. 

In [1]:
###########################################
### Just run this cell to load the data ###
###########################################

import tensorflow_datasets as tfds
from tensorflow.keras.preprocessing.text import text_to_word_sequence

def load_data(percentage_of_sentences=None):
    train_data, test_data = tfds.load(name="imdb_reviews", split=["train", "test"], batch_size=-1, as_supervised=True)

    train_sentences, y_train = tfds.as_numpy(train_data)
    test_sentences, y_test = tfds.as_numpy(test_data)
    
    # Take only a given percentage of the entire data
    if percentage_of_sentences is not None:
        assert(percentage_of_sentences> 0 and percentage_of_sentences<=100)
        
        len_train = int(percentage_of_sentences/100*len(train_sentences))
        train_sentences, y_train = train_sentences[:len_train], y_train[:len_train]
  
        len_test = int(percentage_of_sentences/100*len(test_sentences))
        test_sentences, y_test = test_sentences[:len_test], y_test[:len_test]
    
    X_train = [text_to_word_sequence(_.decode("utf-8")) for _ in train_sentences]
    X_test = [text_to_word_sequence(_.decode("utf-8")) for _ in test_sentences]
    
    return X_train, y_train, X_test, y_test

X_train, y_train, X_test, y_test = load_data(percentage_of_sentences=10)

2022-11-18 11:00:03.378143: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-11-18 11:00:07.168531: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In the previous exercise, we jointly learned a representation for the words, and fed this representation to a RNN, as shown here: 

<img src="layers_embedding.png" width="400px" />

However, this increases the number of parameters to learn, which slows down and increases the difficulty of convergence!

For this reason, we will separate the steps of learning the word representation and feeding it into a RNN. As shown here: 

<img src="word2vec_representation.png" width="400px" />

We will learn the embedding with word2vec.

The drawback is indeed that the learned embeddings are not _specifically_ designed for our task. However, learning them independently of the task at hand (sentiment analysis) has some advantages: 
- it is very fast to do in general (with word2vec)
- the representation learned by word2vec is still meaningful 
- the convergence of the RNN alone will be easier and faster

So let's learn an embedding with word2vec and see how meaningful it is!


# Embedding with Word2Vec

Let's use Word2Vec to embed the words of our sentences. Word2Vec will be able to convert each word to a fixed-size vectorial representation.

For instance, we will have:
- 'dog' --> [0.1, -0.3, 0.8]
- 'cat' --> [-1.1, 2.3, 0.7]
- 'apple' --> [3.1, 0.9, -4.7]

Here, your embedding space is of size 3.

What you expect is to have representation such as words with close meanings are close in this embedding space. As in this example:

![Embedding](word_embedding.png)

❓ **Question** ❓ Let's run Word2Vec! The following code imports word2vec from [GENSIM](https://radimrehurek.com/gensim/), a great python package that makes the use of the word2vec algorithm easy, fast and accurate - which is not an easy task. The second line learns the embedding representation of the words thanks to the sentences in `X_train`. The third line stores the words and their trained embeddings in `wv`.

In [2]:
from gensim.models import Word2Vec

word2vec = Word2Vec(sentences=X_train)
wv = word2vec.wv

Let's look at the embedded representation of some words.

You can use `wv` as a dictionary.
For instance, `wv['dog']` will return a representation of `dog` in the embedding space.

❓ **Question** ❓ Try different words - especially, try non-existing words to see that they don't have any representation (which is perfectly normal as their representation was not learned). 

In [3]:
wv['woman']

array([-0.42436773,  0.26972833, -0.47984865,  0.2586365 ,  0.03197176,
       -0.29549327,  0.06537353,  0.7302433 , -0.12635079, -0.95879275,
       -0.15520889, -0.7154279 , -0.20430903, -0.02132053,  0.02790112,
       -0.00738183, -0.30021235, -0.18189603,  0.01620532,  0.00217148,
       -0.08934583,  0.34016898,  0.07729184, -0.44254565, -0.08422833,
        0.08196475, -0.925045  ,  0.0276898 , -0.15833166, -0.1316718 ,
       -0.10535244, -0.28226605,  0.3737699 , -1.1466197 , -0.3267476 ,
        0.42289996,  0.50086737, -0.27382618, -0.24985138,  0.1715586 ,
       -0.5250902 , -0.5233914 , -1.0841533 ,  0.4438711 ,  0.5391232 ,
       -0.6687179 ,  0.3547674 , -0.16353251,  0.8414693 ,  0.5964042 ,
        0.28378192, -0.80187136, -0.16571218,  0.15442237, -0.4078811 ,
        0.8595975 ,  0.43815967, -0.41200206,  0.08874416,  0.61207366,
        0.40982127,  0.11022649,  0.12466709,  0.15459858,  0.07234588,
        0.47473288,  0.05751964,  0.45731476, -0.4172843 ,  0.47

❓ **Question** ❓ What is the size of each word representation, and therefore, what is the size of the embedding space?

In [4]:
wv['woman'].shape

(100,)

How to know if this embedding make any sense? To do that, we will check that words with a close meaning have close representations. 

Let's use the [`Word2Vec.wv.most_similar`](https://radimrehurek.com/gensim/models/keyedvectors.html#gensim.models.keyedvectors.KeyedVectors.most_similar) method that, given an input word, displays the "closest" words in the embedding space. If the embedding is well done, then words that have similar meanings will have similar representation in the embedding space.

❓ **Question** ❓ Test the `most_similar` method on different words. 

❗ **Remark** ❗ Indeed, the quality of the closeness will depend on the quality of your embedding, and thus, depend on the number of sentences that you have loaded and from which you create your embedding.

In [5]:
wv.most_similar('movie', topn=10)

[('film', 0.9587035775184631),
 ('show', 0.8248674869537354),
 ('thing', 0.8066716194152832),
 ('series', 0.793173611164093),
 ('sequel', 0.7850290536880493),
 ('flick', 0.7599310278892517),
 ('ending', 0.7539215087890625),
 ('improvement', 0.7534855604171753),
 ('book', 0.7406731247901917),
 ('fan', 0.7278326749801636)]

Similarly to `most_similar` used on words directly, we can use [`similar_by_vector`](https://radimrehurek.com/gensim/models/keyedvectors.html#gensim.models.keyedvectors.KeyedVectors.similar_by_vector) on vectors to do the same thing:

In [6]:
wv.similar_by_vector(wv['queen'])

[('queen', 1.0000001192092896),
 ('loving', 0.9892838597297668),
 ('mysterious', 0.9870175719261169),
 ('ben', 0.9869973063468933),
 ('wayne', 0.986821711063385),
 ('winning', 0.9867026209831238),
 ('victim', 0.9865769147872925),
 ('frances', 0.9863220453262329),
 ('tarzan', 0.9862326979637146),
 ('dog', 0.9859409332275391)]

# Arithmetic on words

Now, let's do mathematical operations on words - meaning on their vector representations!

As any word is represented as a vector, you can do basic arithmetic as:

$$W2V(good) - W2V(bad)$$

❓ **Question** ❓ Do this mathematical operation and print the result

In [7]:
v_good = wv["good"]
v_bad  = wv["bad"]

v_result = v_good - v_bad
v_result

array([ 0.16562223, -0.07314928,  0.23658055,  0.3482691 ,  0.01898038,
       -0.06288975, -0.3501715 , -0.18839714,  0.11990523, -0.11800605,
        0.36374018,  0.32433224,  0.27014187, -0.08661395, -0.05412436,
        0.27230373, -0.54939055,  0.2748469 ,  0.02274179,  0.6533581 ,
       -0.21936354, -0.03189251, -0.357234  ,  0.00802667, -0.06058219,
       -0.03412484, -0.22643754,  0.4339053 ,  0.15055281, -0.62061113,
       -0.63520694, -0.01864223,  0.4175257 ,  0.15949474, -0.17960355,
       -0.20499861,  0.46906295, -0.26653165, -0.40200487,  0.60850525,
       -0.2841267 , -0.2107361 , -0.39901853, -0.11226678,  0.40984723,
       -0.17221816,  0.33479273, -0.16119504,  0.01199421,  0.27056056,
       -0.06397337,  0.10813081, -0.78158194, -0.0934177 , -0.05964899,
        0.24177797,  0.09472484,  0.02196484,  0.26391983,  0.17969286,
        0.26331818,  0.25754428, -0.08349204, -0.2817608 ,  0.09903663,
        0.12396097, -0.36780292, -0.12828463,  0.31022716,  0.31

Now, imagine for a second that the following equality holds true:

$$W2V(good) - W2V(bad) = W2V(nice) - W2V(stupid)$$

which is equivalent to:

$$W2V(good) - W2V(bad) + W2V(stupid) = W2V(nice)$$

❓ **Question** ❓ Let's, just for fun (as it would be bold of us to think that this equality holds true ...), do the operation $W2V(good) - W2V(bad) + W2V(stupid)$ and store it in a `res` variable (which will be a vector of size 100 that you can print).

In [8]:
v_good = wv["good"]
v_bad  = wv["bad"]
v_stupid = wv["stupid"]

res = v_good - v_bad + v_stupid
res

array([ 0.3435308 , -0.22055091,  0.426885  ,  0.02350909,  0.07290971,
       -0.5577755 , -0.4693357 ,  0.23594227, -0.38339674, -0.43397927,
        0.14134265, -0.10767969,  0.42104194,  0.23271194,  0.09770726,
        0.0647887 , -0.17446232, -0.21455976, -0.229357  , -0.28785604,
        0.16880235,  0.00670909,  0.3481953 , -0.05747513, -0.13285506,
       -0.20717424, -0.44683468,  0.16535613, -0.02922821, -0.53997767,
       -0.01495624,  0.00408261,  0.7365531 , -0.1642655 , -0.43004033,
        0.56625986,  0.40828645, -0.08741656, -0.58705854, -0.18903697,
       -0.255565  , -0.65776336, -0.25773582,  0.41510475,  0.5545535 ,
       -0.18478425,  0.12866396, -0.5109217 , -0.11592864,  0.4544732 ,
       -0.04562558, -0.04673906, -0.7700949 ,  0.12221728,  0.06488632,
        0.44307578,  0.20065115, -0.04592567, -0.27819997, -0.24219248,
        0.18397985, -0.1709243 ,  0.24710229,  0.10902759, -0.4745189 ,
        0.60719454, -0.1680845 ,  0.05409051, -0.06384069,  0.40

We said earlier, that for any vector it is possible to see the closest vectors in the embedding space.

❓ **Question** ❓ Look at the closest vector (thanks to the `similar_by_vector` function) of `res`

In [9]:
wv.similar_by_vector(res)

[('spark', 0.8008638024330139),
 ('nice', 0.776928186416626),
 ('given', 0.7569577693939209),
 ('successful', 0.7554870843887329),
 ('good', 0.7402191162109375),
 ('carrey', 0.737532913684845),
 ('wonderful', 0.7335426807403564),
 ('also', 0.7322446703910828),
 ('mentioning', 0.7283758521080017),
 ('smart', 0.7269229888916016)]

Incredible right! You can do arithmetic operations on words!

❓ **Question** ❓ You can try on arithmetic such as 

$$W2V(Boy) - W2V(Girl) = W2V(Man) - W2V(Woman)$$

or 

$$W2V(Queen) - W2V(King) = W2V(actress) - W2V(actor)$$

❗ **Remark** ❗ You will probably see that the results are not perfect. But don't forget that you trained your model on a very small corpus.

You might wonder where does this magic comes from (at quite a low price, you just run a line of code on a very small corpus and it was trained within few minutes). The magic comes from the way Word2Vec is trained. The details are quite complex, but you can remember that Word2vec, in `word2vec = Word2Vec(sentences=X_train)`, actually trains a internal neural network (that you don't see).  

In a nutshell, this internal NN predicts a word from the surroundings words in a sentences. So it splits the original sentences, then for each split it chooses some words as inputs $X$ and a word as the output $y$ which it tries to predict, using the embedding space.

And as with any neural network, Word2Vec has some hyperparameters. Let's check some out. 


# Word2Vec hyperparameters


❓ **Question** ❓ The first important hyperparameter is the `vector_size` argument. It corresponds to the size of the embedding space. Learn a new `word2vec_2` model, still trained on the `X_train`, but with a smaller or higher `vector_size`.

Verify on some words that the corresponding embedding is of your selected size.

In [10]:
word2vec2 = Word2Vec(sentences=X_train,vector_size=50)
wv2 = word2vec2.wv

In [11]:
len(wv["dog"])

100

❓ **Question** ❓ Use the `Word2Vec.wv.key_to_index` attribute to display the size of the learned vocabulary. Compare it to the number of different words in `X_train`.

In [12]:
import numpy as np
X_flat = [word for sentence in X_train for word in sentence]
len(wv.key_to_index),len(np.unique(X_flat))

(8006, 30419)

There is an important difference between the number of words in the train sentences and in the Word2Vec vocabulary, even though it has been trained on the train sentence set. The reasons comes from the second important hyperparameter of Word2Vec:  `min_count`. 

`min_count` is a integer that tells you how many occurrences a given word should have to be learned in the embedding space. For instance, let's say that the word "movie" appears 1000 times in the corpus and "simba" only 2 times. If `min_count=3`, the word "simba" will be skipped during the training.

The intention is to have only words that are sufficiently present in the corpus to have a robust embedded representation

❓ **Question** ❓ Learn a new `word2vec_3` model with a `min_count` higher than 5 (which is the default value) and a `word2vec_4` with a `min_count` smaller than 5, and then, compare the size of the vocabulary for all the different word2vecs that you have trained (you can choose any `vector_size` you want).

In [13]:
word2vec3 = Word2Vec(sentences=X_train,vector_size=50,min_count=6)
wv3 = word2vec3.wv

word2vec4 = Word2Vec(sentences=X_train,vector_size=50,min_count=3)
wv4 = word2vec4.wv

len(wv.key_to_index),len(wv3.key_to_index),len(wv4.key_to_index),len(np.unique(X_flat))

(8006, 6892, 12116, 30419)

Remember that we said word2vec has an internal neural network that it optimizes based on some predictions? These predictions actually correspond to predicting a word based on surrounding words. The surroundings words are in a `window` which corresponds to the number of words taken into account. And you can train the word2vec with different `window` sizes.

❓ **Question** ❓ Train a new `word2vec_5` model with a `window` different than previously (default is 5).

In [14]:
word2vec5 = Word2Vec(sentences=X_train,vector_size=50,min_count=6,window=10)
wv5 = word2vec5.wv

The arguments you have seen (`vector_size`, `min_count` and `window`) are usually the ones that you should start changing to get a better performance for your model.

But you can also look at other arguments in the [documentation](https://radimrehurek.com/gensim/models/word2vec.html#gensim.models.word2vec.Text8Corpus)



# Convert our train and test set to RNN ready data

Remember that word2vec is the first step to the overall process of feeding such a representation into a RNN, as shown here:

<img src="word2vec_representation.png" width="400px" />



Now, let's work on Step 2 by converting the training and test data into their vector representation to be ready to be feed in RNNs.

❓ **Question** ❓ Now, write a function that, given a sentence, returns a matrix that corresponds to the embedding of the full sentence, which means that you have to embed each word one after the other and concatenate the result to output a 2D matrix (be sure that your output is a NumPy array)

❗ **Remark** ❗ You will probably notice that some words you are trying to convert throw errors as they are said not to belong to the dictionary:

- for the test set, this is understandable: some words were not in the train set and thus their embedded representation is unknown
- for the train set, due to `min_count` hyperparameter, not all the words have a vector representation

In any case, just skip the missing words here.

In [15]:
import numpy as np

example = ['this', 'movie', 'is', 'the', 'worst', 'action', 'movie', 'ever']
example_missing_words = ['this', 'movie', 'is', 'laaaaaaaaaame']

def embed_sentence(word2vec, sentence):
    arr = []
    for word in sentence:
        try: 
            temp = word2vec.wv[word]
            len(temp)
            arr.append(temp)
        except:
            print(word + " not in corpus or not found more than 5 times")
    return np.array(arr)

### Checks
embedded_sentence = embed_sentence(word2vec, example)
assert(type(embedded_sentence) == np.ndarray)
assert(embedded_sentence.shape == (8, 100))

embedded_sentence_missing_words = embed_sentence(word2vec, example_missing_words)  
assert(type(embedded_sentence_missing_words) == np.ndarray)
assert(embedded_sentence_missing_words.shape == (3, 100))

laaaaaaaaaame not in corpus or not found more than 5 times


❓ **Question** ❓ Write a function that, given a list of sentences (each sentence being a list of words/strings), returns a list of embedded sentences (each sentence is a matrix). Apply this function to the train and test sentences

Hint: Use the previous function `embed_sentence`

In [16]:
def embedding(word2vec, sentences):
    return np.array([embed_sentence(word2vec,sentence) for sentence in sentences])
    
X_train = embedding(word2vec, X_train)
X_test = embedding(word2vec, X_test)

ironside not in corpus or not found more than 5 times
columbian not in corpus or not found more than 5 times
rebels not in corpus or not found more than 5 times
revolutions not in corpus or not found more than 5 times
conchita not in corpus or not found more than 5 times
alonso not in corpus or not found more than 5 times
plug not in corpus or not found more than 5 times
ruining not in corpus or not found more than 5 times
walken's not in corpus or not found more than 5 times
sette not in corpus or not found more than 5 times
accord not in corpus or not found more than 5 times
alberta not in corpus or not found more than 5 times
brennan not in corpus or not found more than 5 times
mountie not in corpus or not found more than 5 times
yukon not in corpus or not found more than 5 times
elect not in corpus or not found more than 5 times
enforce not in corpus or not found more than 5 times
gunfighters not in corpus or not found more than 5 times
klondike not in corpus or not found more than

/var/folders/w5/tx540wbj3xj4gn4n7mgd84hm0000gn/T/ipykernel_40859/3552894283.py:2: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  return np.array([embed_sentence(word2vec,sentence) for sentence in sentences])


detached not in corpus or not found more than 5 times
capshaw not in corpus or not found more than 5 times
capshaw not in corpus or not found more than 5 times
campus not in corpus or not found more than 5 times
irresistibly not in corpus or not found more than 5 times
geraldine not in corpus or not found more than 5 times
mcewan not in corpus or not found more than 5 times
l'ecole not in corpus or not found more than 5 times
chair' not in corpus or not found more than 5 times
'post not in corpus or not found more than 5 times
coitum not in corpus or not found more than 5 times
triste not in corpus or not found more than 5 times
letter' not in corpus or not found more than 5 times
eminently not in corpus or not found more than 5 times
unambitious not in corpus or not found more than 5 times
relying not in corpus or not found more than 5 times
charms not in corpus or not found more than 5 times
dreamworks not in corpus or not found more than 5 times
paved not in corpus or not found more

❓ **Question** ❓ In order to have ready-to-use data, do not forget to pad your sequences so you have tensors that can be divided into batches (of `batch_size`) during the optimization. Store the padded values in `X_train_pad` and `X_test_pad`. Do not forget the important arguments of the padding ;)

In [22]:
from tensorflow.keras.utils import pad_sequences

X_train_pad = pad_sequences(
    X_train,
    maxlen=300,
    dtype=type(X_train[0][0]),
    padding='post',
    value=0
)


X_test_pad = pad_sequences(
    X_test,
    maxlen=300,
    dtype=type(X_train[0][0]),
    padding='post',
    value=0
)



len(X_train_pad[0]),len(X_test_pad[0])

assert(len(X_train_pad.shape) == 3)
assert(len(X_test_pad.shape) == 3)
assert(X_train_pad.shape[2] == 100)
assert(X_test_pad.shape[2] == 100)

In [23]:
X_train_pad.shape

(2500, 300, 100)